In [3]:
from search import *
import math

class riverproblem(Problem):
    
                      
    def __init__(self,initial=((3,3),(0,0),1,0), goal=((0,0),(3,3),0,1)):
        self.goal = goal
        Problem.__init__(self, initial, goal)
    
    #defining a valid state    
    def valid_state(self,state):
        Source,Destination,boatAtSource,boatAtDestination = state
        
        Missionary_Source,Cannibal_Source = Source  # the count of missionaries and cannibals at source
        Missionary_Destination,Cannibal_Destination = Destination # the count of missionaries and cannibals at destination
        
        if Missionary_Source < 0 or Missionary_Destination < 0 or Cannibal_Source < 0 or Cannibal_Destination < 0:
            return False
        if Missionary_Source < Cannibal_Source and Missionary_Source >0:
            return False
        if Missionary_Destination < Cannibal_Destination  and Missionary_Destination > 0:
            return False        
        return True
        
    
    #defining possible actions
    def actions(self, state):
        """ Return the possible actions in any given state.
        The result would be a list 
        """
        possible_actions = []
        Source,Destination,boatAtSource,boatAtDestination = state
        Missionary_Source,Cannibal_Source = Source
        Missionary_Destination,Cannibal_Destination = Destination 
        
        if boatAtSource:
            """Do something"""
            for MissionaryCount,CannibalCount in [(2,0),(1,0),(1,1),(0,1),(0,2)]:
                new_Missionary_Source = Missionary_Source - MissionaryCount
                new_Missionary_Destination = Missionary_Destination + MissionaryCount    
                new_Cannibal_Source = Cannibal_Source - CannibalCount
                new_Cannibal_Destination = Cannibal_Destination + CannibalCount
                    
                new_state = ((new_Missionary_Source,new_Cannibal_Source),(new_Missionary_Destination,new_Cannibal_Destination),1,0)
                if self.valid_state(new_state):
                    action = "Missionary"*MissionaryCount + "Cannibal"*CannibalCount
                    action+="ToDestination"
                    possible_actions.append(action)
            
        elif boatAtDestination:
            """Do something"""
            for MissionaryCount,CannibalCount in [(2,0),(1,0),(1,1),(0,1),(0,2)]:
                new_Missionary_Source = Missionary_Source + MissionaryCount
                new_Missionary_Destination = Missionary_Destination - MissionaryCount    
                new_Cannibal_Source = Cannibal_Source + CannibalCount
                new_Cannibal_Destination = Cannibal_Destination - CannibalCount
                    
                new_state = ((new_Missionary_Source,new_Cannibal_Source),(new_Missionary_Destination,new_Cannibal_Destination),1,0)
                if self.valid_state(new_state):
                    action = "Missionary"*MissionaryCount + "Cannibal"*CannibalCount
                    action+="ToSource"
                    possible_actions.append(action)
        
        return possible_actions
    
    def result(self, state, action):
        """ Given state and action, returns a new state that is the result of the action.
        Action is assumed to be a valid action in the state """
        
        
        Source,Destination,boatAtSource,boatAtDestination = state
        Missionary_Source,Cannibal_Source = Source
        Missionary_Destination,Cannibal_Destination = Destination 
        
        if boatAtSource:
            """Do something"""
            if action == "CannibalCannibalToDestination":
                Cannibal_Source-=2
                Cannibal_Destination+=2
            elif action =="CannibalToDestination":
                Cannibal_Source-=1
                Cannibal_Destination+=1
            elif action =="MissionaryMissionaryToDestination":
                Missionary_Source-=2
                Missionary_Destination+=2
            elif action =="MissionaryToDestination":
                Missionary_Source-=1
                Missionary_Destination+=1
            elif action =="MissionaryCannibalToDestination":
                Cannibal_Source-=1
                Cannibal_Destination+=1
                Missionary_Source-=1
                Missionary_Destination+=1
            new_state = ((Missionary_Source,Cannibal_Source),(Missionary_Destination,Cannibal_Destination),0,1)
            
        elif boatAtDestination:
            """Do something"""
            if action == "CannibalCannibalToSource":
                Cannibal_Source+=2
                Cannibal_Destination-=2
            elif action =="CannibalToSource":
                Cannibal_Source+=1
                Cannibal_Destination-=1
            elif action =="MissionaryMissionaryToSource":
                Missionary_Source+=2
                Missionary_Destination-=2
            elif action =="MissionaryToSource":
                Missionary_Source+=1
                Missionary_Destination-=1
            elif action =="MissionaryCannibalToSource":
                Cannibal_Source+=1
                Cannibal_Destination-=1
                Missionary_Source+=1
                Missionary_Destination-=1
            new_state = ((Missionary_Source,Cannibal_Source),(Missionary_Destination,Cannibal_Destination),1,0)
        return tuple(new_state)

    def goal_test(self, state):
        """ Check if a given state is goal, returns if True and returns False if not """
        return state == self.goal
    
    
    def h(self, node):
        """ creating a heuristic to check the total # of people shipped from source to destination """
        return (sum(node.state[0]))


# In[12]:


def best_first_graph_search_show_frontier(problem, f,showFrontier = True):
    """Search the nodes with the lowest f scores first.
    You specify the function f(node) that you want to minimize; for example,
    if f is a heuristic estimate to the goal, then we have greedy best
    first search; if f is node.depth then we have breadth-first search.
    There is a subtlety: the line "f = memoize(f, 'f')" means that the f
    values will be cached on the nodes as they are computed. So after doing
    a best first search you can examine the f values of the path returned."""
    f = memoize(f, 'f')
    node = Node(problem.initial)
    frontier = PriorityQueue('min', f)
    frontier.append(node)
    explored = set()
    while frontier:
        if showFrontier:
            print("Explored list ==>",explored) 
            print("Frontier list ==> ",frontier.heap)
            print("\n")
        node = frontier.pop()
        if problem.goal_test(node.state):
            return node

        explored.add(node.state)
        for child in node.expand(problem):
            if child.state not in explored and child not in frontier:
                frontier.append(child)
            elif child in frontier:
                if f(child) < frontier[child]:
                    del frontier[child]
                    frontier.append(child)
        
    return None


# In[13]:


def astar_search_show_frontier(problem, h=None):
    """A* search is best-first graph search with f(n) = g(n)+h(n).
    You need to specify the h function when you call astar_search, or
    else in your Problem subclass."""
    h = memoize(h or problem.h, 'h')
    return best_first_graph_search_show_frontier(problem, lambda n: n.path_cost*2 + h(n))


# In[14]:


def recursive_best_first_search_show_frontier(problem, h=None):
    """[Figure 3.26]"""
    h = memoize(h or problem.h, 'h')
    """Rbf sometimes goes too deep so we will take a step to store all the steps into files 
    we are calling it rbfs_missionay_canibals.txt """
    def RBFS(problem, node, f_limit):
        if problem.goal_test(node.state):
            return node, 0  # (The second value is immaterial)
        successors = node.expand(problem)
        if len(successors) == 0:
            return None, infinity
        for s in successors:
            """changed path cost to 2 """
            s.f = max(s.path_cost*2 + h(s), node.f)
        while True:
            # Order by lowest f value
            successors.sort(key=lambda x: x.f)
            best = successors[0]
            if len(successors) > 1:
                alternative = successors[1].f
            else:
                alternative = math.inf
            print("f_limit = "+str(f_limit))
            print("best = "+str(best.f))
            print("alternative = "+str(alternative))
            print("Current state - "+str(node.state))
            if best.f > f_limit:
                print("Failure! Backtracking")    
                print("\n")
                return None, best.f
            else:
                print("Next state - "+str(successors[0].state))
                print("\n")
            
            result, best.f = RBFS(problem, best, min(f_limit, alternative))
            if result is not None:
                return result, best.f
            
    node = Node(problem.initial)
    node.f = h(node)
    result, bestf = RBFS(problem, node, math.inf)
    return result


# In[15]:


def uniform_cost_search_with_frontier(problem):
    """[Figure 3.14]"""
    return best_first_graph_search_show_frontier(problem, lambda node: node.path_cost)


# In[16]:


def iterative_deepening_search_with_frontier(problem):
    """[Figure 3.18]"""
    for depth in range(sys.maxsize):
        result = depth_limited_search_with_frontier(problem, depth)
        if result != 'cutoff':
            return result


# In[17]:


def depth_limited_search_with_frontier(problem, limit=50):
    """[Figure 3.17]"""
    print("Depth limit = ",limit)
    def recursive_dls(node, problem, limit, frontier, explored=set({})):
        print("Depth",limit)
        print("Current state",node.state)
        explored.add(node.state)
        if node.state in frontier:
            frontier.remove(node.state)
        if problem.goal_test(node.state):
            print("Goal state !!!\n")
            return node
        elif limit == 0:
            print('A cutoff as occured\n')
            return 'cutoff'
        else:
            cutoff_occurred = False
            for child in node.expand(problem):
                frontier.add(child.state)
            print("Frontier list==> ",frontier)
            print("Explored list ==> ",explored)
            print("\n")
            for child in node.expand(problem):
                result = recursive_dls(child, problem, limit - 1, frontier, explored)
                if result == 'cutoff':
                    cutoff_occurred = True
                elif result is not None:
                    return result
                else:
                    explored.add(child.state)
                    if child.state in frontier:
                        frontier.remove(child.state)
            return 'cutoff' if cutoff_occurred else None
    
    # Body of depth_limited_search:
    return recursive_dls(Node(problem.initial), problem, limit,frontier=set({Node(problem.initial).state}))


# # Uniform Cost Search

# In[19]:


puzzle = riverproblem()
print("\n\nUniform Cost Search Problem solution\n")
path = uniform_cost_search_with_frontier(puzzle).solution()
print("The path is -> ",path)


# # Iterative Deepening Search

# In[20]:


print("\n\nIterative Deepening search solution\n")
path = iterative_deepening_search_with_frontier(puzzle).solution()
print("path solution ==>",path)


# #  Greedy Best First Search

# In[22]:


print("\n\nGreedy Best First Search solution\n")
path = best_first_graph_search_show_frontier(puzzle,lambda node: sum(node.state[0])).solution()
print("The path is ==>",path)


# #  A* search 

# In[23]:


print("\nA* search solution\n")
path = astar_search_show_frontier(puzzle).solution()
print("The path is  ==>",path)


# # Recursive Best First Search

# In[24]:


print("\n\nRBFS solution\n")
# just to clear all the content of the file
path = recursive_best_first_search_show_frontier(puzzle).solution()
print("path solution ==>",path)




Uniform Cost Search Problem solution

Explored list ==> set()
Frontier list ==>  [(0, <Node ((3, 3), (0, 0), 1, 0)>)]


Explored list ==> {((3, 3), (0, 0), 1, 0)}
Frontier list ==>  [(1, <Node ((2, 2), (1, 1), 0, 1)>), (1, <Node ((3, 2), (0, 1), 0, 1)>), (1, <Node ((3, 1), (0, 2), 0, 1)>)]


Explored list ==> {((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1)}
Frontier list ==>  [(1, <Node ((3, 1), (0, 2), 0, 1)>), (1, <Node ((3, 2), (0, 1), 0, 1)>), (2, <Node ((3, 2), (0, 1), 1, 0)>)]


Explored list ==> {((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}
Frontier list ==>  [(1, <Node ((3, 2), (0, 1), 0, 1)>), (2, <Node ((3, 2), (0, 1), 1, 0)>)]


Explored list ==> {((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}
Frontier list ==>  [(2, <Node ((3, 2), (0, 1), 1, 0)>)]


Explored list ==> {((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Frontier li

Current state ((3, 2), (0, 1), 1, 0)
A cutoff as occured

Depth 4
Current state ((3, 3), (0, 0), 1, 0)
Frontier list==>  {((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 3
Current state ((2, 2), (1, 1), 0, 1)
Frontier list==>  {((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 2
Current state ((3, 2), (0, 1), 1, 0)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (

Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1)}


Depth 4
Current state ((2, 2), (1, 1), 0, 1)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1)}


Depth 3
Current state ((3, 2), (0, 1), 1, 0)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((2, 2), (1, 1), 0, 1)}


Depth 2
Current state ((2, 2), (1, 1), 0, 1)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 2)


Depth 3
Current state ((3, 2), (0, 1), 1, 0)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((0, 2), (3, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 2
Current state ((2, 2), (1, 1), 0, 1)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((0, 2), (3, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 1
Current state ((3, 2), (0, 1), 1, 0)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0,

Frontier list==>  {((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((0, 2), (3, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 1
Current state ((3, 2), (0, 1), 1, 0)
Frontier list==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 3), (0, 0), 1, 0), ((3, 1), (0, 2), 0, 1)}
Explored list ==>  {((3, 0), (0, 3), 0, 1), ((2, 2), (1, 1), 0, 1), ((3, 1), (0, 2), 1, 0), ((2, 2), (1, 1), 1, 0), ((3, 2), (0, 1), 0, 1), ((3, 2), (0, 1), 1, 0), ((3, 3), (0, 0), 1, 0), ((1, 1), (2, 2), 0, 1), ((0, 2), (3, 1), 0, 1), ((3, 1), (0, 2), 0, 1)}


Depth 0
Current state ((2, 2), (1, 1), 0, 1)
A cutoff as occured

Depth 0
Current state ((3, 1), (0, 2), 0, 1)
A cutoff as occured

Depth 0
Current state ((3, 0), (0, 3), 0, 1)
A cutoff as occured

Depth 1
Current state ((3, 3), (0, 0), 1, 0)
Fronti

...


f_limit = 22
best = 22
alternative = 22
Current state - ((2, 2), (1, 1), 0, 1)
Next state - ((3, 2), (0, 1), 1, 0)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((2, 2), (1, 1), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((2, 2), (1, 1), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((3, 1), (0, 2), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((3, 1), (0, 2), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 25
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((3, 0), (0, 3), 0, 1)


f_limit = 22
best = 24
alternative = 25
Current state - ((3, 0), (0, 3), 0, 1)
Failure! Backtracking


f_limit = 22
best = 24
alternative = 25
Current state - ((3, 2), (0, 1), 1, 0)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 24
Current state - ((2, 2), (1, 1), 0, 1)
Next state - ((3, 3), (0, 0), 1, 0)


f_



f_limit = 22
best = 25
alternative = 26
Current state - ((3, 1), (0, 2), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 25
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((3, 0), (0, 3), 0, 1)


f_limit = 22
best = 24
alternative = 25
Current state - ((3, 0), (0, 3), 0, 1)
Failure! Backtracking


f_limit = 22
best = 24
alternative = 25
Current state - ((3, 2), (0, 1), 1, 0)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 24
Current state - ((2, 2), (1, 1), 0, 1)
Next state - ((3, 3), (0, 0), 1, 0)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 3), (0, 0), 1, 0)
Next state - ((2, 2), (1, 1), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((2, 2), (1, 1), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 23
Current state - ((3, 3), (0, 0), 1, 0)
Next state - ((3, 1), (0, 2), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((3, 1), (0, 2), 0, 1)
Failure! Backtracking


f_limit = 22
be

f_limit = 22
best = 22
alternative = 23
Current state - ((3, 3), (0, 0), 1, 0)
Next state - ((3, 1), (0, 2), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((3, 1), (0, 2), 0, 1)
Failure! Backtracking


f_limit = 22
best = 23
alternative = 25
Current state - ((3, 3), (0, 0), 1, 0)
Failure! Backtracking


f_limit = 22
best = 23
alternative = inf
Current state - ((3, 2), (0, 1), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 23
Current state - ((3, 3), (0, 0), 1, 0)
Next state - ((3, 1), (0, 2), 0, 1)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 1), (0, 2), 0, 1)
Next state - ((3, 2), (0, 1), 1, 0)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((2, 2), (1, 1), 0, 1)


f_limit = 22
best = 25
alternative = 26
Current state - ((2, 2), (1, 1), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((3, 1), (0, 2), 0, 1)


f_

alternative = 24
Current state - ((3, 1), (0, 2), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 23
Current state - ((3, 2), (0, 1), 1, 0)
Next state - ((3, 0), (0, 3), 0, 1)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 0), (0, 3), 0, 1)
Next state - ((3, 1), (0, 2), 1, 0)


f_limit = 22
best = 22
alternative = 22
Current state - ((3, 1), (0, 2), 1, 0)
Next state - ((1, 1), (2, 2), 0, 1)


f_limit = 22
best = 24
alternative = 24
Current state - ((1, 1), (2, 2), 0, 1)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 24
Current state - ((3, 1), (0, 2), 1, 0)
Next state - ((3, 0), (0, 3), 0, 1)


f_limit = 22
best = 24
alternative = 25
Current state - ((3, 0), (0, 3), 0, 1)
Failure! Backtracking


f_limit = 22
best = 24
alternative = 24
Current state - ((3, 1), (0, 2), 1, 0)
Failure! Backtracking


f_limit = 22
best = 22
alternative = 24
Current state - ((3, 0), (0, 3), 0, 1)
Next state - ((3, 2), (0, 1), 1, 0)


f_limit = 22
best = 22
alt

path solution ==> ['MissionaryCannibalToDestination', 'MissionaryToSource', 'CannibalCannibalToDestination', 'CannibalToSource', 'MissionaryMissionaryToDestination', 'MissionaryCannibalToSource', 'MissionaryMissionaryToDestination', 'CannibalToSource', 'CannibalCannibalToDestination', 'MissionaryToSource', 'MissionaryCannibalToDestination']
